In [4]:
import pandas as pd
import datetime
import numpy as np

import pickle
from signals import *
from dealManager import *
from trandeVoter import *
from riskManager import riskManager

In [5]:
df_candle = pd.read_csv("../data/EURUSD_price_candlestick.csv")
df_candle.rename(columns={'timestamp': 'date'}, inplace=True)
df_candle

date     open    close     high      low
0      2020-09-01 03:00:00+03:00  1.19370  1.19388  1.19391  1.19368
1      2020-09-01 03:00:05+03:00  1.19387  1.19388  1.19391  1.19383
2      2020-09-01 03:00:10+03:00  1.19387  1.19384  1.19389  1.19382
3      2020-09-01 03:00:15+03:00  1.19384  1.19384  1.19386  1.19382
4      2020-09-01 03:00:20+03:00  1.19387  1.19390  1.19391  1.19383
...                          ...      ...      ...      ...      ...
99995  2020-09-06 21:52:55+03:00  1.18382  1.18382  1.18393  1.18371
99996  2020-09-06 21:53:00+03:00  1.18382  1.18382  1.18393  1.18371
99997  2020-09-06 21:53:05+03:00  1.18382  1.18382  1.18393  1.18371
99998  2020-09-06 21:53:10+03:00  1.18382  1.18382  1.18393  1.18371
99999  2020-09-06 21:53:15+03:00  1.18382  1.18382  1.18393  1.18371

[100000 rows x 5 columns]

In [6]:
class decsionManager():

    
    def __init__(self,name):
        self.name = name
        self.RM = riskManager()
        self.DM = DealManager()
        self.TV = trandeVoter(name)
        self.SA = signalAgrigator()
        pass
    
    #вытащенный из signalAgrigator метод теста для сигналов
    def getSignalTest(self,data: pd.DataFrame(),reqSig: dict, batchSize=30, dataType='candel') -> dict:
        
        self.SA.mode = 'retroFast'
        t.SA.createSingnalInstances(
            data = data,
            dictAgrigSignal = reqSig,
            dataType='candel',
            batchSize=30
        )
        ans = t.SA.getAns(data)
        return ans
    
    #метод для генерации матрицы вероятностей.
    def generateMatrixProbability(self, 
                                  data: pd.DataFrame(),
                                  reqSig: dict, 
                                  target: str, 
                                  batchSize=30, 
                                  #dataType='candel'
                                 ):
        data=data.reset_index(drop=True)
        
        t.SA.createSingnalInstances(
            data = data,
            dictAgrigSignal = reqSig,
            dataType='candel',
            batchSize=batchSize
        )
        self.TV.createMatrixAmounts(reqSig.keys())
        for i in range(data.shape[0]-batchSize-1):
            sigAns=self.SA.getAns(data[i:i+batchSize])
            rightAns=self.getRetroStepAns(data[target][i],data[target][i+1])
            self.TV.setDecisionBySignals(self.KostilEbaniy(sigAns),rightAns)
        self.TV.generateMatrixProbability()
    
    #без коментариев блять
    def KostilEbaniy(self,d):
        ans={}
        for i in d.keys():
            if d[i] == 0:
                ans[i] = 'none'
            elif d[i] == 1:
                ans[i] = 'up'
            elif d[i] == -1:
                ans[i] = 'down'
        return ans
    
    #тож понятная хуита
    def getRetroStepAns(self, value1,value2):
        
        if value1 == value2:
            ans = 'none'
        elif value1 < value2:
            ans = 'up'
        else:
            ans = 'down'
        return ans
        
    #метод для онлай получения решения по сигналу
    def getSignal(self,data: pd.DataFrame(),reqSig: dict, dataType='candel') -> dict:
        data=data.reset_index(drop=True)
        self.SA.mode = 'online'
        t.SA.createSingnalInstances(
            data = data,
            dictAgrigSignal = reqSig,
            dataType='candel',
            batchSize=30
        )
        ans = t.SA.getAns(data)
        return ans        
    
    
    #Создание сигналов. Вызывать перед getOnlineAns
    def crateSignals(self,data: pd.DataFrame(),reqSig: dict, dataType='candel'):
        data=data.reset_index(drop=True)
        self.SA.mode = 'online'
        t.SA.createSingnalInstances(
            data = data,
            dictAgrigSignal = reqSig,
            dataType='candel',
            batchSize=30
        )
        
    
    def getOnlineAns(self,data: pd.DataFrame(),price):
        sigAns = self.SA.getAns(data)
        prob = self.TV.getDecisionBySignals(sigAns)
        ans = self.RM.getDecision(sigAns,prob,price)
        return ans
        
        
        
        


In [7]:
t= decsionManager('TEST')

In [8]:
t.__dict__

{'name': 'TEST',
 'RM': <riskManager.riskManager at 0x7fda34bbd2d0>,
 'DM': <dealManager.DealManager at 0x7fda134d6590>,
 'TV': <trandeVoter.trandeVoter at 0x7fda34b8ef90>,
 'SA': <signals.signalAgrigator at 0x7fda1ff34950>}

In [9]:
reqSig={
    'BB1':{
        'className':signal_BB,
        'indParams':{'MeanType':'SMA','window':15,'valueType':'close','kDev':2.5},
        'signalParams':{'source':'close','target':'close'},
        'batchSize':15
    },
    'BB2':{
        'className':signal_BB,
        'indParams':{'MeanType':'SMA','window':15,'valueType':'close','kDev':2.5},
        'signalParams':{'source':'close','target':'close'},
        'batchSize':20
    }
}

In [10]:
reqSig.keys()

dict_keys(['BB1', 'BB2'])

In [11]:
t.SA.__dict__

{'signalsInstances': {}, 'mode': 'online'}

In [12]:
t.generateMatrixProbability(df_candle[:10000],reqSig,'close',40)

Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
S

/home/parf/projects/marketTrade/MVP/trandeVoter.py:48: RuntimeWarning:

invalid value encountered in scalar divide

/home/parf/projects/marketTrade/MVP/trandeVoter.py:49: RuntimeWarning:

invalid value encountered in scalar divide

/home/parf/projects/marketTrade/MVP/trandeVoter.py:50: RuntimeWarning:

invalid value encountered in scalar divide



Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
P

Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
P

Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
P

...

Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
P

Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
P

Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
P

Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
Processing DONE!
Start processing...
P

C:\Users\Redsandy\PyProj\Trade\MVP\trandeVoter.py:48: RuntimeWarning:

invalid value encountered in longlong_scalars

C:\Users\Redsandy\PyProj\Trade\MVP\trandeVoter.py:49: RuntimeWarning:

invalid value encountered in longlong_scalars

C:\Users\Redsandy\PyProj\Trade\MVP\trandeVoter.py:50: RuntimeWarning:

invalid value encountered in longlong_scalars



In [13]:
mop = t.TV.matrixProbability
mop

up      none      down
BB1  BB2                               
up   up    0.391304  0.254658  0.354037
     none       NaN       NaN       NaN
     down       NaN       NaN       NaN
none up         NaN       NaN       NaN
     none  0.380035  0.239826  0.380139
     down       NaN       NaN       NaN
down up         NaN       NaN       NaN
     none       NaN       NaN       NaN
     down  0.382979  0.290780  0.326241

In [14]:
t.getSignal(df_candle[:10000],reqSig)

Start processing...
Processing DONE!
Start processing...
Processing DONE!


{'BB1': 0, 'BB2': 0}

In [15]:
t.getSignalTest(df_candle[:10000],reqSig,40)

Start processing...


100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 9969/9969 [00:18<00:00, 538.21it/s]


Start analiz...
Analiz DONE!
Processing DONE!
Start processing...


100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 9969/9969 [00:17<00:00, 555.09it/s]


Start analiz...
Analiz DONE!
Processing DONE!


{'BB1': {'softAnaliz': {'1': 0.030293911124485907, '2': -0.007021767479185475},
  'hardAnaliz': {'1': 1.0, '2': -0.5074731668171331}},
 'BB2': {'softAnaliz': {'1': 0.030293911124485907, '2': -0.007021767479185475},
  'hardAnaliz': {'1': 1.0, '2': -0.5074731668171331}}}

In [16]:
t.SA.createSingnalInstances(
    data = df_candle[:10000],
    dictAgrigSignal = reqSig,
    dataType='candel',
    batchSize=30
)

{'BB1': <signals.signal_BB at 0x7fda135fa450>,
 'BB2': <signals.signal_BB at 0x7fda135fb790>}

In [17]:
reqSig={
    'BB1':{
        'className':signal_BB,
        'indParams':{'MeanType':'SMA','window':15,'valueType':'close','kDev':2.5},
        'signalParams':{'source':'close','target':'close'},
        'batchSize':15
    },
    'BB2':{
        'className':signal_BB,
        'indParams':{'MeanType':'SMA','window':15,'valueType':'close','kDev':2.5},
        'signalParams':{'source':'close','target':'close'},
        'batchSize':20
    }
}

In [18]:
t=decsionManager(reqSig)

In [ ]:
import pickle

In [ ]:
dictionary_data = {"a": 1, "b": 2}


a_file = open("data.pkl", "wb")

pickle.dump(reqSig, a_file)

a_file.close()


a_file = open("data.pkl", "rb")

output = pickle.load(a_file)

print(output)



a_file.close()